In [189]:
from selenium import webdriver
from bs4 import BeautifulSoup
import csv
import re
import codecs
import nltk

BRANDS_MAX_DISTANCE = 2
MAX_WORD_DISTANCE = 4

COMMENTS_AMOUNT = 4000

forumUrl = 'https://forums.edmunds.com/discussion/2864/general/x/entry-level-luxury-performance-sedans/p{}'

In [342]:
def get_first_comments(amount=COMMENTS_AMOUNT):
    messages = []
#     driver = webdriver.Chrome('C:\\Users\\lovek\\Documents\\UGCA_assignment\\chromedriver_win32\\chromedriver.exe')
    driver = webdriver.Chrome('./chromedriver')
    for pageNum in range(700):
        driver.get(forumUrl.format(pageNum))
        rawPageContents = driver.page_source
        soup = BeautifulSoup(rawPageContents, 'html.parser')
        #messages.extend(get_page_messages(soup))
        elements = soup.find_all('div',{'class':'Message'})
        for elem in elements:
            try:
                elem.blockquote.decompose()
            except:
                None
        messages.extend(map(lambda msgElement: msgElement.text.strip(),elements))
        if len(messages) >= COMMENTS_AMOUNT:
            break
    return messages

In [92]:
def get_models_replace_map():
    brands = set()
    replace_map = {}
    pattern = re.compile('[\W_]+')
    with codecs.open('models.csv','r' ,encoding='utf-8', errors='ignore') as f:
        for row in csv.DictReader(f,fieldnames=['brand','model']):
            
            model = row['model'].replace('\xa0', '')
            brand = row['brand'].replace('\xa0', '')
            brand = pattern.sub('', brand)
            brand = get_closest_brand(brand,list(brands))
            brands.add(brand)
            
            replace_map[model] = brand
        return replace_map

In [343]:
def get_closest_brand(brand,brands):
    for b in brands:
        if nltk.edit_distance(brand,b)<=BRANDS_MAX_DISTANCE:
            return b
    return brand

In [93]:
def apply_model_brand_replacements(messages,replace_map):
    manipulated_messages = []
    for message in messages:
        manipulated_message = message
        for model,brand in replace_map.items():
            re_expression = re.compile(r'\b{}\b'.format(re.escape(model)), re.IGNORECASE)
            manipulated_message = re_expression.sub(brand, manipulated_message)
        manipulated_messages.append(manipulated_message)
    return manipulated_messages


In [94]:
replace_map = get_models_replace_map()


In [95]:
messages = get_first_comments()
manipulated_messages = apply_model_brand_replacements(messages,replace_map)

In [96]:
listofBrands=[(v,0) for k,v in replace_map.items()]
unique_brands=list(set(listofBrands))

wrong_entries = ['car','problem','sedan', 'hyndai kia']

brands_dict = dict((x,y) for x, y in unique_brands if x not in (wrong_entries))
brands_dict

{'subaru': 0,
 'mercedes': 0,
 'chevrolet': 0,
 'cadillac': 0,
 'audi': 0,
 'hyundai,': 0,
 'dodge': 0,
 'seat': 0,
 'mercury': 0,
 'pontiac': 0,
 'ford': 0,
 'nissan': 0,
 'honda': 0,
 'lincoln': 0,
 'toyota': 0,
 'saturn': 0,
 'hyundai': 0,
 'infiniti': 0,
 'chrysler': 0,
 'buick': 0,
 'bmw': 0,
 'hyundai.': 0,
 'kia': 0,
 'acura': 0,
 'kia.': 0,
 'mitsubishi': 0,
 'volkswagen': 0,
 'suzuki': 0,
 'volvo': 0,
 'mercedes-benz': 0,
 'volkwagen': 0,
 'mazda': 0,
 'nissan.': 0,
 'toyata': 0}

In [101]:
#Count the brand name once per message is it appears in the message
for message in manipulated_messages:
    lowerCaseMessage=message.lower()
    #print(lowerCaseMessage)
    for k,v in brands_dict.items():
        if k in lowerCaseMessage:
            brands_dict[k]+=1

In [102]:
top_brands_byfreq = sorted(brands_dict.items(), key=lambda kv: kv[1], reverse=True)[:10]
top_brands_byfreq

[('bmw', 2107),
 ('acura', 939),
 ('audi', 683),
 ('infiniti', 649),
 ('honda', 597),
 ('nissan', 485),
 ('seat', 474),
 ('toyota', 403),
 ('ford', 375),
 ('mercedes', 316)]

In [216]:
def get_brands_pairs_counts(messages,brands,pairs_counts):
    for message in messages:
        message = message.lower()
        message_brands = extract_elements(message,brands)
        brands_pairs = list(itertools.combinations(message_brands,2))
        brands_pairs = filter_pairs_by_distance(message,brands_pairs)
        increment_brands_pairs(brands_pairs,pairs_counts)
        
def get_brands_attributes_pairs_counts(messages,brands,attributes,pairs_counts):
    for message in messages:
        message = message.lower()
        message_brands = extract_elements(message,brands)
        message_attributes = extract_elements(message,attributes)
        brands_attributes_pairs = list(itertools.product(message_brands, message_attributes))
        brands_attributes_pairs = filter_pairs_by_distance(message,brands_attributes_pairs)
        increment_brands_pairs(brands_attributes_pairs,pairs_counts)

def filter_pairs_by_distance(message,brands_pairs):
    filtered_brands_pairs = []
    for brand1,brand2 in brands_pairs:
        for sentence in sent_tokenize(message):
            words_distance = get_words_distance(sentence, brand1, brand2)
            if words_distance is not None and words_distance <= MAX_WORD_DISTANCE:
                filtered_brands_pairs.append((brand1,brand2))
                break
    return filtered_brands_pairs
            
def get_words_distance(sentence, w1, w2):
    global stop_words
    words = [word for word in word_tokenize(sentence) if word not in stop_words]
    if w1 in words and w2 in words:
        return abs(words.index(w2) - words.index(w1))
        
def extract_elements(message,elements):
    words = word_tokenize(message)
    #We sort the brands in order to get sorted combinations and eliminate duplicates
    return set(sorted([word for word in words if word in elements]))

In [195]:
def increment_brands_pairs(brands_pairs,pairs_counts):
    for brand_pair in brands_pairs:
        pairs_counts[brand_pair] = pairs_counts.get(brand_pair, 0) + 1

In [147]:
import itertools

# dict which will contain brand pair as keys and count
brand_pair = {}
brand_name=brands_dict.keys()
brand_pair_lst=[]

# for each message traverse which all brands are their and form a key (2 - brand name) # if key exist in dict, increment else add with value 1
for message in manipulated_messages:
    message = message.lower()

# tp is list that contain one whole message
    tp = message.split()
    temp_brand = []

# for all word in one message if it is a brand append it to temp_brnd
    for word in tp:
        if word in brand_name:
            #print(word)
            temp_brand.append(word)
            temp_brand = list(set(temp_brand))
            # brand_pair_lst will contain all the combinations
            brand_pair_lst = list(itertools.combinations(temp_brand,2))
            # check dict keys and form it
        for pairs in brand_pair_lst:
            if pairs in brand_pair.keys():
                brand_pair[pairs] = brand_pair[pairs] + 1
            else:
                brand_pair[pairs] = 1

In [148]:
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
stop_words = set(stopwords.words('english'))

In [173]:
brand_pair

{}

In [217]:
# dict which will contain brand pair as keys and count
brand_pair = {}
brands=brand_pair.keys()
brands_pairs_counts = {}
brands_attributes_pairs_counts = {}
# for each message traverse which all brands are their and form a key (2 - brand name) # if key exist in dict, increment else add with value 1
messages = map(lambda message: message.lower(), messages)

top_brands = [item[0] for item in top_brands_byfreq]

get_brands_pairs_counts(manipulated_messages,top_brands,brands_pairs_counts)

pp = pprint.PrettyPrinter(depth=6)

#pp.pprint(brands_pairs_counts)

entry level performance luxury sedan are a hot area for car manufacturers and enthusiasts alike. acura bmw
these sedan show their performance by being fun to drive and handling well. acura bmw
they show luxury by offering leather and some of the important creatures comforts found in the most luxurious upscale sedan. acura bmw
the selection of vehicles that compete in the space is vast and varied.the benchmarks which define this are the bmw 330 and the audi audi 3.0.  but there are many contenders, such as acura tl-s, chrysler chrysler, jaguar x-type, infiniti i35, mercedes-benz mercedes-benz, volvo volvo t5. acura bmw
some companies have contenders that emphasize performance lexus is300 or luxury lexus es300. acura bmw
and the field is continously growing, with the recent additions being the cadillac cts and infiniti g35.the common charateristics of this entry level perfomance luxury group seem to a price around 30 to 40k (us dollars) and 0-60 times between six and eight seconds.with t

they are actually selling a fwd x-type in england and i've read where they're thinking about selling it here! bmw audi
hell no. bmw audi
the car should have been rwd not awd. bmw audi
some will tell you that this was done to compete with audi. bmw audi
thats bs, awd was the only way to keep the car from being fwd, without spending the money to convert the car to rwd. bmw audi
it is a good looking car though and that jaguar "leaper" will be enough for some, but this car has to grow on me. bmw audi
the chrysler chrysler is about as close to an audi that american car come. bmw audi
this new chrysler "special" is truly a good looking car inside and out. bmw audi
one problem: where is the performance???? bmw audi
a 255hp car *in this class) with a 0-60 time over 8 seconds is not accpetable. bmw audi
something is not right here. bmw audi
some say engine, transmission and/or gearing, but whatever it is, chrysler needs to let some mb engineers have a look at this car. bmw audi
the heavier e320

but from what i noticed is that some bmw "supportors" don't even own a bmw, (at least not from their profile) or they state that they never drove an infiniti g35, but they still make "unsupported" facts, assumptions or opinions on such. bmw toyota
(see the edmund's bmw bmw discussion). bmw toyota
i hope in your defense, toyota, that you drove the automatic infiniti g35, to give an opinionated statement that it doesn't classify as a performance sedan. bmw toyota
i value your opinion and others as well.again, i'm not flaming you, but i try to be an informed consumer before i buy anything. bmw toyota
that is the reason that i will drive every car that i'm interested in and make my choice from there. bmw toyota
i'm also always interested in those opinions from people that own the type of car i'm shopping for and at least drove it, so they can give valid pro/negative statements.cheers! bmw toyota
>"is there such a thing as an automatic-only true performance sedan? infiniti audi
not in my bo

thats bs, awd was the only way to keep the car from being fwd, without spending the money to convert the car to rwd. acura seat
it is a good looking car though and that jaguar "leaper" will be enough for some, but this car has to grow on me. acura seat
the chrysler chrysler is about as close to an audi that american car come. acura seat
this new chrysler "special" is truly a good looking car inside and out. acura seat
one problem: where is the performance???? acura seat
a 255hp car *in this class) with a 0-60 time over 8 seconds is not accpetable. acura seat
something is not right here. acura seat
some say engine, transmission and/or gearing, but whatever it is, chrysler needs to let some mb engineers have a look at this car. acura seat
the heavier e320 with less power is faster. acura seat
i still like this car, but it's no lust object once you get past the great styling. acura seat
m acura seat
i personally think that with a few tweaks the c320 could also sit at the top of this group

i was kind of dissappointed by the 2002 facelift, they could have done a little more in the way of styling. audi seat
i hope they do a little more for 2003 with the coupe models. audi seat
the acura tl-s is easily my favorite fwd car in this class. audi seat
wonderful engine (you actually can hear it) and decent handling for a front driver. audi seat
nice price, seat and what not, not hard to see why the tl is so popular. audi seat
this car's main faults are styling and obvious cost-cutting in the interior, stereo, fake wood etc. audi seat
otherwise a standout. audi seat
lexus es300. audi seat
nice, but not my type of car at all. audi seat
this is one for the buick set. audi seat
the is300 is half baked, but has a wonderful chassis. audi seat
styling is also in question here, it simply doesn't look like a 35k car (grown). audi seat
the interior is gawd-awful. audi seat
bet on the next is300 being done right from the start. audi seat
in their defense toyota didn't initially intend for t

...

i considered the is300, but no dealers in my area had any manuals in stock, and none of them had any on order, nor were they planning on adding any to their inventory, ever.the acura and audi are fwd...the bmw was pretty much the only choice.i'd gone seven years without a car payment. acura audi
i bought my 325i in january because i bought a 318ti back in august of 1995.  ten years on and that ti still drives like new. acura toyota
over those ten years it had one mechanical failure (the ignition switch went bad) apart from the usual wear-and-tear items (batteries, tires, etc.) acura toyota
i hated the idea of trading it in so much that i put off buying a new car for as long as i could. acura toyota
then it hit me: buy a new car and don't trade in the ti.i came close to buying a mb c230 late last year but the deal fell through. acura toyota
i looked at the g35, but they told me the manuals wouldn't be out until february. acura toyota
i considered the is300, but no dealers in my area had

it almost seemed people are afraid to question bmw's, since it's been foolishly jamed into minds...bmw's are "high performance, high quality...". bmw audi
mostly by magazines(press), friends(who like the label), and the high price to own.but as these posts say, it's mostly opinion, and actually, bmw's probably aren't worth the high price for similar performance.one thing i still don't see many people admitting, is bmw, benzes, and audi's low reliability and high cost of maintanance. bmw audi
i feel this is in the direction of pride. bmw audi
no one likes to admit cost paid, vs more cost spent to maintain.and it is fact, bmw's do break down more then average, consumeraffairs.com/news03/jdpower.html little old (2003)mercedes-benz clsdiff class2002and it does cost more once it's in shop (vs asian, us brands). bmw audi
of course it depends who drives, but when the car is in the shop, pull out the wallet. bmw audi
one of the biggest problem that i have with folks who like to take issue with

as a single gal, that might play into things a bit. bmw infiniti
i'll have to weigh in on the side of the tl - here's some general comments (no particular order), and i include a little scoring system (+1 for 1st, 0 for 2nd, -1 for 3rd) that's really just for my own fun.:1. bmw toyota
ride quality. bmw toyota
as far as ride quality, i'd guess you prefer a cushier, luxurious ride to a sporty, tight ride. bmw toyota
the used gs430 your considering would probably have the best ride, but with all the high-tech features you want, the tl would probably be a good compromise between toyota, price and features. bmw toyota
the g35 has the most sporty, probably least forgiving ride of the 3. bmw toyota
(gs 1; tl  0; g35 -1)2.  status. bmw toyota
i think acura has the least status among lexus, infiniti and acura. bmw toyota
i think lexus is #1 of those 3, so the gs has it here, too. bmw toyota
(gs 2; tl -1; g35 -1)3.  features. bmw toyota
the used gs isn't going to be the most technologically adva

the exterior of the car doesn't influence my purchase. audi honda
for god's sake i owned a protege until last month. audi honda
people will still buy it for performance, which is understandable, but will close eyes on styling. audi honda
some auto magazine writers also not so excited about new 3 style.i'm not closing my eyes. audi honda
it just doesn't matter to me. audi honda
i can't grasp the rancor over the pontiac or the hype surrounding the solstice. audi honda
the same question comes back: "but how does it drive?" audi honda
the ford gt reminds me of the only version of the 'stang i ever felt anything visceral for (the stocker), but the car's suspension set up and engine make me dubious of the car. audi honda
sure one can mod it to look like something out of 'road warrior" but how does it perform? audi honda
that's the end all and be all of the equation.back to work...fun break... audi honda
if you want to burn $50k and a toyota.... well...i would suggest looking at a gs430 with 

one last thing you have to remember that the new 325i and 330i was aimed at the infiniti g35 and that the g35 was aimed at the older 2005 and before model. honda audi
therefore i think there will be a crown toss between infiniti and bmw for many years to come not to say acura and audi and mb wont come out with future great products ! honda audi
also with the great new manumatic type trans i believe that the auto's are fun to drive and have that universal appeal of highway driving and honda driving its great ! honda audi
2006 330i sedan     destination charge$695    exterior  monaco blue metallic  $475   interior  gray dakota leather   included   aluminum trim    packages sport package   $1,600  premium package   $2,200  cold weather package   $1,000   msrp   $36,300   price as configured$46,265  options steptronic automatic transmission   $1,275  on-board navigation system w/idrive   $2,000  satellite radio   $595  carpeted floor mats   $125  that was with none of the interesting gizmo

In [218]:
brands_pairs_counts

{('bmw', 'audi'): 57,
 ('bmw', 'infiniti'): 49,
 ('infiniti', 'audi'): 10,
 ('infiniti', 'toyota'): 2,
 ('acura', 'nissan'): 6,
 ('acura', 'infiniti'): 45,
 ('bmw', 'nissan'): 7,
 ('honda', 'toyota'): 66,
 ('acura', 'honda'): 29,
 ('audi', 'infiniti'): 3,
 ('acura', 'audi'): 18,
 ('bmw', 'seat'): 9,
 ('audi', 'seat'): 3,
 ('toyota', 'honda'): 1,
 ('acura', 'bmw'): 37,
 ('acura', 'seat'): 1,
 ('bmw', 'toyota'): 12,
 ('toyota', 'seat'): 3,
 ('nissan', 'infiniti'): 7,
 ('honda', 'infiniti'): 3,
 ('bmw', 'honda'): 10,
 ('nissan', 'honda'): 31,
 ('honda', 'nissan'): 12,
 ('nissan', 'toyota'): 29,
 ('nissan', 'audi'): 3,
 ('ford', 'audi'): 1,
 ('toyota', 'nissan'): 1,
 ('ford', 'honda'): 4,
 ('ford', 'nissan'): 3,
 ('audi', 'honda'): 2,
 ('ford', 'toyota'): 4,
 ('infiniti', 'honda'): 3,
 ('bmw', 'ford'): 6,
 ('acura', 'toyota'): 5,
 ('acura', 'ford'): 1,
 ('ford', 'infiniti'): 1,
 ('ford', 'seat'): 1}

In [270]:
def calculate_lift(elements_pairs_counts,elements_freqs,num_of_messages):
    lift_values = {}
    for elements_pair,times in elements_pairs_counts.items():
        pair_lift = ((num_of_messages * times)*1.0)/(elements_freqs[elements_pair[0]]*elements_freqs[elements_pair[1]])
        lift_values[elements_pair] = float(round(pair_lift,2))
    return lift_values

In [271]:
def merge_two_dicts(x, y):
    z = x.copy()
    z.update(y)
    return z

In [272]:
def merge_two_dicts(x, y):
    z = x.copy()
    z.update(y)
    return z

In [341]:
lift_values = calculate_lift(brands_pairs_counts,dict(top_brands_byfreq),len(manipulated_messages))
top_lift_values = sorted(lift_values.items(), key=lambda kv: kv[1], reverse=False)[:10]
pp.pprint(top_lift_values)

[(('acura', 'seat'), 0.01),
 (('acura', 'ford'), 0.01),
 (('toyota', 'honda'), 0.02),
 (('ford', 'audi'), 0.02),
 (('toyota', 'nissan'), 0.02),
 (('audi', 'honda'), 0.02),
 (('ford', 'infiniti'), 0.02),
 (('ford', 'seat'), 0.02),
 (('infiniti', 'toyota'), 0.03),
 (('bmw', 'nissan'), 0.03)]


In [340]:
lift_values

{('bmw', 'audi'): 0.16,
 ('bmw', 'infiniti'): 0.14,
 ('infiniti', 'audi'): 0.09,
 ('infiniti', 'toyota'): 0.03,
 ('acura', 'nissan'): 0.05,
 ('acura', 'infiniti'): 0.3,
 ('bmw', 'nissan'): 0.03,
 ('honda', 'toyota'): 1.1,
 ('acura', 'honda'): 0.21,
 ('audi', 'infiniti'): 0.03,
 ('acura', 'audi'): 0.11,
 ('bmw', 'seat'): 0.04,
 ('audi', 'seat'): 0.04,
 ('toyota', 'honda'): 0.02,
 ('acura', 'bmw'): 0.08,
 ('acura', 'seat'): 0.01,
 ('bmw', 'toyota'): 0.06,
 ('toyota', 'seat'): 0.06,
 ('nissan', 'infiniti'): 0.09,
 ('honda', 'infiniti'): 0.03,
 ('bmw', 'honda'): 0.03,
 ('nissan', 'honda'): 0.43,
 ('honda', 'nissan'): 0.17,
 ('nissan', 'toyota'): 0.6,
 ('nissan', 'audi'): 0.04,
 ('ford', 'audi'): 0.02,
 ('toyota', 'nissan'): 0.02,
 ('ford', 'honda'): 0.07,
 ('ford', 'nissan'): 0.07,
 ('audi', 'honda'): 0.02,
 ('ford', 'toyota'): 0.11,
 ('infiniti', 'honda'): 0.03,
 ('bmw', 'ford'): 0.03,
 ('acura', 'toyota'): 0.05,
 ('acura', 'ford'): 0.01,
 ('ford', 'infiniti'): 0.02,
 ('ford', 'seat'): 0.

In [274]:
brands_dict

{'subaru': 289,
 'mercedes': 316,
 'chevrolet': 89,
 'cadillac': 206,
 'audi': 683,
 'hyundai,': 18,
 'dodge': 77,
 'seat': 474,
 'mercury': 14,
 'pontiac': 70,
 'ford': 375,
 'nissan': 485,
 'honda': 597,
 'lincoln': 109,
 'toyota': 403,
 'saturn': 21,
 'hyundai': 176,
 'infiniti': 649,
 'chrysler': 115,
 'buick': 60,
 'bmw': 2107,
 'hyundai.': 27,
 'kia': 46,
 'acura': 939,
 'kia.': 0,
 'mitsubishi': 35,
 'volkswagen': 176,
 'suzuki': 21,
 'volvo': 246,
 'mercedes-benz': 206,
 'volkwagen': 2,
 'mazda': 154,
 'nissan.': 57,
 'toyata': 0}

In [314]:
import numpy as np
import matplotlib.pyplot as plt
from sklearn import manifold
import pandas as pd 

brands_list = sorted([key for key in brands_dict])


lift_table = pd.DataFrame(index=brands_list)
i = 0
for brand_row in lift_table.index:
    lift_table[brand_row] = ['x' for i in range(len(brands_list))]

for brand_1,brand_2 in lift_values:
    lift_table.loc[brand_1][brand_2] = float(lift_values[brand_1,brand_2])

for brand_row in lift_table.index:
    for brand_column in lift_table.index:
        if isinstance(lift_table.loc[brand_row][brand_column], float) and \
        isinstance(lift_table.loc[brand_column][brand_row], str):
            lift_table.loc[brand_column][brand_row] = float(lift_table.loc[brand_row][brand_column])
        if isinstance(lift_table.loc[brand_row][brand_column], str) and \
        isinstance(lift_table.loc[brand_column][brand_row], str):
            lift_table.loc[brand_column][brand_row] = float(1.0)
            lift_table.loc[brand_row][brand_column] = float(1.0)            

for brand_row in lift_table.index:
    for brand_column in lift_table.index:
        if brand_row != brand_column:
            lift_table.loc[brand_column][brand_row] = float(1 / (lift_table.loc[brand_column][brand_row]))
        else:
            lift_table.loc[brand_column][brand_row] = float(0.0)

In [315]:
lift_table

acura     audi      bmw buick cadillac chevrolet chrysler  \
acura                0  9.09091     12.5     1        1         1        1   
audi           9.09091        0     6.25     1        1         1        1   
bmw               12.5     6.25        0     1        1         1        1   
buick                1        1        1     0        1         1        1   
cadillac             1        1        1     1        0         1        1   
chevrolet            1        1        1     1        1         0        1   
chrysler             1        1        1     1        1         1        0   
dodge                1        1        1     1        1         1        1   
ford               100       50  33.3333     1        1         1        1   
honda           4.7619       50  33.3333     1        1         1        1   
hyundai              1        1        1     1        1         1        1   
hyundai,             1        1        1     1        1         1        1   
hyundai.             1        1        1     1        1         1        1   
infiniti       3.33333  11.1111  7.14286     1        1         1        1   
kia                  1        1        1     1        1         1        1   
kia.                 1        1        1     1        1         1        1   
lincoln              1        1        1     1        1         1        1   
mazda                1        1        1     1        1         1        1   
mercedes             1        1        1     1        1         1        1   
mercedes-benz        1        1        1     1        1         1        1   
mercury              1        1        1     1        1         1        1   
mitsubishi           1        1        1     1        1         1        1   
nissan              20       25  33.3333     1        1         1        1   
nissan.              1        1        1     1        1         1        1   
pontiac              1        1        1     1        1         1        1   
saturn               1        1        1     1        1         1        1   
seat               100       25       25     1        1         1        1   
subaru               1        1        1     1        1         1        1   
suzuki               1        1        1     1        1         1        1   
toyata               1        1        1     1        1         1        1   
toyota              20        1  16.6667     1        1         1        1   
volkswagen           1        1        1     1        1         1        1   
volkwagen            1        1        1     1        1         1        1   
volvo                1        1        1     1        1         1        1   

              dodge     ford    honda  ...  pontiac saturn     seat subaru  \
acura             1      100   4.7619  ...        1      1      100      1   
audi              1       50       50  ...        1      1       25      1   
bmw               1  33.3333  33.3333  ...        1      1       25      1   
buick             1        1        1  ...        1      1        1      1   
cadillac          1        1        1  ...        1      1        1      1   
chevrolet         1        1        1  ...        1      1        1      1   
chrysler          1        1        1  ...        1      1        1      1   
dodge             0        1        1  ...        1      1        1      1   
ford              1        0  14.2857  ...        1      1       50      1   
honda             1  14.2857        0  ...        1      1        1      1   
hyundai           1        1        1  ...        1      1        1      1   
hyundai,          1        1        1  ...        1      1        1      1   
hyundai.          1        1        1  ...        1      1        1      1   
infiniti          1       50  33.3333  ...        1      1        1      1   
kia               1        1        1  ...        1      1        1      1   
kia.              1        1        1 

In [316]:
dists = []
for column in lift_table:
    dists.append(list(lift_table.loc[column]))
dists

[[0.0,
  9.090909090909092,
  12.5,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  100.0,
  4.761904761904762,
  1.0,
  1.0,
  1.0,
  3.3333333333333335,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  20.0,
  1.0,
  1.0,
  1.0,
  100.0,
  1.0,
  1.0,
  1.0,
  20.0,
  1.0,
  1.0,
  1.0],
 [9.090909090909092,
  0.0,
  6.25,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  50.0,
  50.0,
  1.0,
  1.0,
  1.0,
  33.333333333333336,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  25.0,
  1.0,
  1.0,
  1.0,
  25.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0],
 [12.5,
  6.25,
  0.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  33.333333333333336,
  33.333333333333336,
  1.0,
  1.0,
  1.0,
  7.142857142857142,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  33.333333333333336,
  1.0,
  1.0,
  1.0,
  25.0,
  1.0,
  1.0,
  1.0,
  16.666666666666668,
  1.0,
  1.0,
  1.0],
 [1.0,
  1.0,
  1.0,
  0.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1

In [344]:
adist = np.array(dists)
amax = np.amax(adist)
adist /= amax



In [ ]:
mds = manifold.MDS(n_components=2, dissimilarity="precomputed", random_state=6)
results = mds.fit(adist.astype(np.float64))


coords = results.embedding_

plt.subplots_adjust(bottom = 0.1)
plt.scatter(
    coords[:, 0], coords[:, 1], marker = 'o'
    )
for label, x, y in zip(brands_list, coords[:, 0], coords[:, 1]):
    plt.annotate(
        label,
        xy = (x, y), xytext = (-20, 20),
        textcoords = 'offset points', ha = 'right', va = 'bottom',
        bbox = dict(boxstyle = 'round,pad=0.5', fc = 'yellow', alpha = 0.5),
        arrowprops = dict(arrowstyle = '->', connectionstyle = 'arc3,rad=0'))

plt.show()

In [46]:
#Used to get word count frequency and transfer data onto csv file and then get list of attributes
# import nltk, re, pprint
# from nltk import word_tokenize
# def tokenize(message):
#     words=word_tokenize(message)
#     return words
# import enchant
# englishDictionary = enchant.Dict("en_US") 
# import nltk
# # Get English stopwords and print some of them
# sw = nltk.corpus.stopwords.words('english')

# word_list=[]
# flattened_list=[]
# for message in messages:
#     lowerCaseMessage=message.lower()
#     result=tokenize(message)
#     word_list.append(result)
    
# for x in word_list:
#     for y in x:
#         if len(y) > 1 and y not in sw  and englishDictionary.check(y)==True:
#             flattened_list.append(y)    
            
# from collections import Counter
# counts={}
# counts = Counter(flattened_list)
# print(counts)

# import csv
# w = csv.writer(open("output.csv", "w"))
# for key, val in counts.items():
#     print(key,value)
#     w.writerow([key, val])



In [112]:
attribute_list=['luxury','steering','interior','price','engine','steer','speed','transmission','make','look','wheel','type','availablility','condition','performance','sale','model','safety','market','color','reliability','technology']
listofAttributes=dict((v,0) for v in attribute_list)

In [113]:
def attribute_replace_map():
    replace_map = {}
    with codecs.open('output.csv','r' ,encoding='utf-8', errors='ignore') as f:
        replace_map = {row['original'].replace('\xa0', ''): row['replacement'].replace('\xa0', '') for row in csv.DictReader(f,fieldnames=['original','replacement'])}
        return replace_map

In [114]:
replace_attribute = attribute_replace_map()

In [115]:
replace_attribute

{'BMW': 'brand',
 'manual': 'transmission',
 'Audi': 'brand',
 'new': 'condition',
 'Jaguar': 'brand',
 'sedan': 'type',
 'Lexus': 'brand',
 'engine': 'performance',
 'looking': 'look',
 'sedans': 'type',
 'power': 'performance',
 'test': 'safety',
 'torque': 'performance',
 'value': 'price',
 'leather': 'interior',
 'styling': 'make',
 'quality': 'make',
 'automatic': 'transmission',
 'mph': 'speed',
 'sales': 'sale',
 'class': 'condition',
 'Japanese': 'brand',
 'made': 'make',
 'Jag': 'brand',
 'hard': 'interior',
 'wood': 'interior',
 'auto': 'transmission',
 'automatics': 'transmission',
 'Toyota': 'brand',
 'American': 'brand',
 'Sport': 'type',
 'looks': 'look',
 'used': 'condition',
 'start': 'engine',
 'old': 'condition',
 'seats': 'interior',
 'money': 'price',
 'style': 'make',
 'sports': 'type',
 'year': 'model',
 'acceleration': 'performance',
 'Chrysler': 'brand',
 'Mercedes': 'brand',
 'Cadillac': 'brand',
 'suspension': 'transmission',
 'models': 'model',
 'faster': 'sp

In [116]:
manipulated_messages_attribute = apply_model_brand_replacements(manipulated_messages,replace_attribute)

In [117]:
manipulated_messages_attribute

['Entry level performance luxury type are a make interior for car brand and enthusiasts alike.  These type show their performance by being fun to drive and handling well.  They show luxury by offering interior and some of the important creatures comforts found in the most luxury luxury type. The selection of vehicles that compete in the interior is market and varied.The benchmarks which define this are the brand 330 and the brand brand 3.0.  But there are many contenders, such as Acura TL-S, brand brand, brand X-type, Infiniti I35, brand-benz brand-benz, brand brand T5.  Some brand have contenders that emphasize performance brand IS300 or luxury brand ES300.  And the field is continously growing, with the condition additions being the brand CTS and Infiniti G35.The common charateristics of this entry level perfomance luxury group seem to a price around 30 to 40k (US price) and 0-60 times between six and eight seconds.With this wide variety of car targeted at a similar market segment, t

In [118]:
for message in manipulated_messages_attribute:
    lowerCaseMessage=message.lower()
    for value in attribute_list:
        if value in lowerCaseMessage:
            listofAttributes[value]+=1

In [119]:
listofAttributes

{'luxury': 440,
 'steering': 2,
 'interior': 855,
 'price': 941,
 'engine': 242,
 'steer': 248,
 'speed': 714,
 'transmission': 616,
 'make': 1343,
 'look': 827,
 'wheel': 467,
 'type': 985,
 'availablility': 93,
 'condition': 1134,
 'performance': 1385,
 'sale': 303,
 'model': 729,
 'safety': 495,
 'market': 245,
 'color': 64,
 'reliability': 484,
 'technology': 57}

In [120]:
top_attr_byfreq = sorted(listofAttributes.items(), key=lambda kv: kv[1], reverse=True)[:5]
top_attr_byfreq

[('performance', 1385),
 ('make', 1343),
 ('condition', 1134),
 ('type', 985),
 ('price', 941)]

In [345]:
top_attributes = [item[0] for item in top_attr_byfreq]
get_brands_attributes_pairs_counts(manipulated_messages_attribute,brands,top_attributes,brands_attributes_pairs_counts)
lift_values = calculate_lift(brands_attributes_pairs_counts,merge_two_dicts(dict(top_attr_byfreq),brands_dict),len(manipulated_messages_attribute))
top_lift_values = sorted(lift_values.items(), key=lambda kv: kv[1], reverse=True)[:10]


In [335]:
manipulated_messages_attribute

['Entry level performance luxury type are a make interior for car brand and enthusiasts alike.  These type show their performance by being fun to drive and handling well.  They show luxury by offering interior and some of the important creatures comforts found in the most luxury luxury type. The selection of vehicles that compete in the interior is market and varied.The benchmarks which define this are the brand 330 and the brand brand 3.0.  But there are many contenders, such as Acura TL-S, brand brand, brand X-type, Infiniti I35, brand-benz brand-benz, brand brand T5.  Some brand have contenders that emphasize performance brand IS300 or luxury brand ES300.  And the field is continously growing, with the condition additions being the brand CTS and Infiniti G35.The common charateristics of this entry level perfomance luxury group seem to a price around 30 to 40k (US price) and 0-60 times between six and eight seconds.With this wide variety of car targeted at a similar market segment, t

In [250]:
punctuations = ['(',')',';',':','[',']',',']

In [251]:
brand_name=list(brands_dict.keys())
brand_name = [''.join(c for c in s if c not in punctuations) for s in brand_name]

brand_name = list(set(brand_name))

In [252]:
brand_name

['buick',
 'bmw',
 'honda',
 'lincoln',
 'mitsubishi',
 'suzuki',
 'audi',
 'nissan',
 'infiniti',
 'hyundai',
 'kia',
 'nissan.',
 'toyota',
 'acura',
 'kia.',
 'mazda',
 'volkswagen',
 'subaru',
 'cadillac',
 'chevrolet',
 'hyundai.',
 'ford',
 'mercedes',
 'chrysler',
 'toyata',
 'volvo',
 'mercury',
 'pontiac',
 'mercedes-benz',
 'volkwagen',
 'dodge',
 'saturn',
 'seat']

In [255]:
import itertools

In [256]:
attributes = ['luxury','steering','interior','price','engine','steer','speed','transmission','make','look','brand','wheel','type','availablility','condition','performance','sale','model','safety','market','color','reliability','technology']

In [262]:
# brand_attribute_pair = {}
# brand_name
brand_attribute_pair_pos = {bn:[] for bn in brand_name}
brand_attribute_pair_neg = {bn:[] for bn in brand_name}
# brand_attribute_pair_ntr = {bn:[] for bn in brand_name}

# brand_attribute_pair = {}

pos_adj = ['good', 'awesome', 'nice', 'better', 'great', 'well', 'best', 'class', 'right']
neg_adj = ['n\'t', 'not', 'bad', 'wrong']

check_senti = []

for mes in manipulated_messages_attribute:
    mes = mes.lower()
    tp = mes.split()
    brnd_name_tmp = []
    
    for wrd in tp:
        if wrd in brand_name:
            brnd_name_tmp.append(wrd)
            
    brnd_name_tmp = list(set(brnd_name_tmp))
            
    for br_name in brnd_name_tmp:
        for i in range(len(tp)):
            check_senti = []
            if tp[i] in attributes:
                if i < 5:
                    if i > len(tp)-6:
                        ckeck_senti = tp
                    else:
                        check_senti = tp[0:i+6]
                else:
                    if i > len(tp)-6:
                        ckeck_senti = tp[i-5:len(tp)]
                    else:
                        check_senti = tp[i-5:i+6]
            
            if len(list(set(check_senti).intersection(neg_adj))) >= 1:
                brand_attribute_pair_neg[br_name].append(tp[i])
            elif len(list(set(check_senti).intersection(pos_adj))) >= 1:
                brand_attribute_pair_pos[br_name].append(tp[i])
#             elif len(check_senti) >= 1:
#                 brand_attribute_pair_ntr[br_name].append(tp[i])
                
#             print(tp)
#             print("this is check_senti")
#             print(check_senti)

In [263]:
temp_dict = {}
for k, v in brand_attribute_pair_pos.items():
    temp_dict[k] = len(v)

In [264]:
df_pos_brand = pd.DataFrame.from_dict(temp_dict, orient='index',columns=['cnt_attr'])

In [265]:
df_pos_brand.sort_values(['cnt_attr'], ascending=False)

cnt_attr
acura               228
infiniti            199
seat                151
volkswagen           81
subaru               74
hyundai              49
buick                30
chevrolet            26
suzuki               21
mazda                19
kia                  14
dodge                13
pontiac              11
hyundai.              8
mitsubishi            7
saturn                3
mercury               3
kia.                  0
bmw                   0
audi                  0
volkwagen             0
mercedes-benz         0
nissan                0
volvo                 0
toyata                0
chrysler              0
mercedes              0
ford                  0
lincoln               0
nissan.               0
toyota                0
honda                 0
cadillac              0

In [348]:
set(brand_attribute_pair_pos['acura'])

{'brand',
 'condition',
 'engine',
 'interior',
 'look',
 'luxury',
 'make',
 'market',
 'model',
 'performance',
 'price',
 'reliability',
 'safety',
 'sale',
 'speed',
 'steer',
 'technology',
 'transmission',
 'type',
 'wheel'}